In [1]:
import pandas as pd
import os
import numpy as np
import scipy
import math
import random
import sklearn
import nltk
import warnings
import matplotlib.pyplot as plt
from nltk.corpus import stopwords
from scipy.sparse import csr_matrix
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from scipy.sparse.linalg import svds
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import MultiLabelBinarizer
from sklearn.metrics import roc_curve, auc

In [2]:
# Set display options to show full content
pd.set_option('display.max_columns', None)  # Show all columns
pd.set_option('display.max_rows', None)     # Show all rows
pd.set_option('display.max_colwidth', None) # Show full content of each column

In [3]:
cwd = os.getcwd()
input = cwd + "\\input\\"

In [4]:
df_keywords = pd.read_csv(input+"cleaned\\keywords.csv")
df_movies = pd.read_csv(input+"cleaned\\movies_metadata.csv")
df_ratings = pd.read_csv(input+"ratings_small.csv")

In [5]:
df_keywords.head()

id  \
0    862   
1   8844   
2  15602   
3  31357   
4  11862   

                                                                                                                  keywords  
0                              jealousy, toy, boy, friendship, friends, rivalry, boy next door, new toy, toy comes to life  
1                                     board game, disappearance, based on children's book, new home, recluse, giant insect  
2                                                                      fishing, best friend, duringcreditsstinger, old men  
3                                            based on novel, interracial relationship, single mother, divorce, chick flick  
4  baby, midlife crisis, confidence, aging, daughter, mother daughter relationship, pregnancy, contraception, gynecologist

In [6]:
df_movies.head()

id                        title release_date  adult  \
0    862                    Toy Story   1995-10-30  False   
1   8844                      Jumanji   1995-12-15  False   
2  15602             Grumpier Old Men   1995-12-22  False   
3  31357            Waiting to Exhale   1995-12-22  False   
4  11862  Father of the Bride Part II   1995-02-10  False   

            belongs_to_collection                      genres  runtime  \
0            Toy Story Collection   Animation, Comedy, Family     81.0   
1                             NaN  Adventure, Fantasy, Family    104.0   
2       Grumpy Old Men Collection             Romance, Comedy    101.0   
3                             NaN      Comedy, Drama, Romance    127.0   
4  Father of the Bride Collection                      Comedy    106.0   

  original_language  \
0                en   
1                en   
2                en   
3                en   
4                en   

                                                                                                                                                                                                                                                                                                                                                                                                      overview  \
0                                                                                              Led by Woody, Andy's toys live happily in his room until Andy's birthday brings Buzz Lightyear onto the scene. Afraid of losing his place in Andy's heart, Woody plots against Buzz. But when circumstances separate Buzz and Woody from their owner, the duo eventually learns to put aside their differences.   
1  When siblings Judy and Peter discover an enchanted board game that opens the door to a magical world, they unwittingly invite Alan -- an adult who's been trapped inside the game for 26 years -- into their living room. Alan's only hope for freedom is to finish the game, which proves risky as all three find themselves running from giant rhinoceroses, evil monkeys and other terrifying creatures.   
2                                                                      A family wedding reignites the ancient feud between next-door neighbors and fishing buddies John and Max. Meanwhile, a sultry Italian divorcée opens a restaurant at the local bait shop, alarming the locals who worry she'll scare the fish away. But she's less interested in seafood than she is in cooking up a hot time with Max.   
3                                                                                                                               Cheated on, mistreated and stepped on, the women are holding their breath, waiting for the elusive "good man" to break a string of less-than-stellar lovers. Friends and confidants Vannah, Bernie, Glo and Robin talk it all out, determined to find a better way to breathe.   
4                                                                               Just when George Banks has recovered from his daughter's wedding, he receives the news that she's pregnant ... and that George's wife, Nina, is expecting too. He was planning on selling their home, but that's a plan that -- like George -- will have to change with the arrival of both a grandchild and a kid of his own.   

                                        production_companies  \
0                                    Pixar Animation Studios   
1  TriStar Pictures, Teitler Film, Interscope Communications   
2                               Warner Bros., Lancaster Gate   
3                     Twentieth Century Fox Film Corporation   
4                 Sandollar Productions, Touchstone Pictures   

       production_countries   spoken_languages      revenue    budget  \
0  United States of America            English  373554033.0  30000000   
1  United States of America  English, Français  262797249.0  65000000   
2  United States of America           

In [7]:
df_ratings.head()

userId  movieId  rating   timestamp
0       1       31     2.5  1260759144
1       1     1029     3.0  1260759179
2       1     1061     3.0  1260759182
3       1     1129     2.0  1260759185
4       1     1172     4.0  1260759205

In [8]:
users_interactions_count_df = df_ratings.groupby(['userId', 'movieId']).size().groupby('userId').size()
print('# users: %d' % len(users_interactions_count_df))

users_with_enough_interactions_df = users_interactions_count_df[users_interactions_count_df >= 5]\
                                    .reset_index()[['userId']]


users_with_few_interactions_df = users_interactions_count_df[users_interactions_count_df < 3]\
                                    .reset_index()[['userId']]

print('# users with at least 5 interactions: %d' % len(users_with_enough_interactions_df))
print('# users with less than 3 interactions: %d' % len(users_with_few_interactions_df))

# users: 671
# users with at least 5 interactions: 671
# users with less than 3 interactions: 0


In [9]:
interactions_from_selected_users_df = df_ratings.merge(users_with_enough_interactions_df, 
               how = 'right',
               left_on = 'userId',
               right_on = 'userId')

interactions_from_few_selected_users_df = df_ratings.merge(users_with_few_interactions_df, 
               how = 'right',
               left_on = 'userId',
               right_on = 'userId')

print('# of interactions from all users: %d' % len(df_ratings))
print('# of interactions from users with at least 5 interactions: %d' % len(interactions_from_selected_users_df))
print('# of interactions from users with less than 3 interactions: %d' % len(interactions_from_few_selected_users_df))

# of interactions from all users: 100004
# of interactions from users with at least 5 interactions: 100004
# of interactions from users with less than 3 interactions: 0


In [12]:
def smooth_user_preference(x):
    return math.log(1+x, 2)
    
interactions_full_df = interactions_from_selected_users_df \
                    .groupby(['userId', 'movieId'])['rating'].sum() \
                    .apply(smooth_user_preference).reset_index()
print('# of unique user/item interactions: %d' % len(interactions_full_df))
interactions_full_df.head(10)

# of unique user/item interactions: 100004


userId  movieId    rating
0       1       31  1.807355
1       1     1029  2.000000
2       1     1061  2.000000
3       1     1129  1.584963
4       1     1172  2.321928
5       1     1263  1.584963
6       1     1287  1.584963
7       1     1293  1.584963
8       1     1339  2.169925
9       1     1343  1.584963

## Top-N Accuracy Metric Evaluation

In [13]:
interactions_train_df, interactions_test_df = train_test_split(interactions_full_df,
                                   stratify=interactions_full_df['userId'], 
                                   test_size=0.20,
                                   random_state=42)

print('# interactions on Train set: %d' % len(interactions_train_df))
print('# interactions on Test set: %d' % len(interactions_test_df))

# interactions on Train set: 80003
# interactions on Test set: 20001


In [35]:
#Indexing by personId to speed up the searches during evaluation
interactions_full_indexed_df = interactions_full_df.set_index('userId')
interactions_train_indexed_df = interactions_train_df.set_index('userId')
interactions_test_indexed_df = interactions_test_df.set_index('userId')

In [14]:
def get_items_interacted(userId, interactions_df):
    # Get the user's data and merge in the movie information.
    interacted_items = interactions_df.loc[userId]['movieId']
    return set(interacted_items if type(interacted_items) == pd.Series else [interacted_items])

In [39]:
#Top-N accuracy metrics consts
EVAL_RANDOM_SAMPLE_NON_INTERACTED_ITEMS = 100

class ModelEvaluator:
    def get_not_interacted_items_sample(self, userId, sample_size, seed=42):
        interacted_items = get_items_interacted(userId, interactions_full_indexed_df)
        all_items = set(df_movies['movieId'])
        non_interacted_items = all_items - interacted_items

        random.seed(seed)
        non_interacted_items_sample = random.sample(non_interacted_items, sample_size)
        return set(non_interacted_items_sample)

    def _verify_hit_top_n(self, item_id, recommended_items, topn):        
            try:
                index = next(i for i, c in enumerate(recommended_items) if c == item_id)
            except:
                index = -1
            hit = int(index in range(0, topn))
            return hit, index

    def evaluate_model_for_user(self, model, userId):
        #Getting the items in test set
        interacted_values_testset = interactions_test_indexed_df.loc[userId]
        if type(interacted_values_testset['movieId']) == pd.Series:
            person_interacted_items_testset = set(interacted_values_testset['movieId'])
        else:
            person_interacted_items_testset = set([int(interacted_values_testset['movieId'])])  
        interacted_items_count_testset = len(person_interacted_items_testset) 

        #Getting a ranked recommendation list from a model for a given user
        user_recs_df = model.recommend_items(userId, 
                                               items_to_ignore=get_items_interacted(userId, 
                                                                                    interactions_train_indexed_df), 
                                               topn=10000000000)

        hits_at_5_count = 0
        hits_at_10_count = 0
        #For each item the user has interacted in test set
        for item_id in person_interacted_items_testset:
            #Getting a random sample (100) items the user has not interacted 
            #(to represent items that are assumed to be no relevant to the user)
            non_interacted_items_sample = self.get_not_interacted_items_sample(userId, 
                                                                          sample_size=EVAL_RANDOM_SAMPLE_NON_INTERACTED_ITEMS, 
                                                                          seed=item_id%(2**32))

            #Combining the current interacted item with the 100 random items
            items_to_filter_recs = non_interacted_items_sample.union(set([item_id]))

            #Filtering only recommendations that are either the interacted item or from a random sample of 100 non-interacted items
            valid_recs_df = person_recs_df[person_recs_df['movieId'].isin(items_to_filter_recs)]                    
            valid_recs = valid_recs_df['movieId'].values
            #Verifying if the current interacted item is among the Top-N recommended items
            hit_at_5, index_at_5 = self._verify_hit_top_n(item_id, valid_recs, 5)
            hits_at_5_count += hit_at_5
            hit_at_10, index_at_10 = self._verify_hit_top_n(item_id, valid_recs, 10)
            hits_at_10_count += hit_at_10

        #Recall is the rate of the interacted items that are ranked among the Top-N recommended items, 
        #when mixed with a set of non-relevant items
        recall_at_5 = hits_at_5_count / float(interacted_items_count_testset)
        recall_at_10 = hits_at_10_count / float(interacted_items_count_testset)

        person_metrics = {'hits@5_count':hits_at_5_count, 
                          'hits@10_count':hits_at_10_count, 
                          'interacted_count': interacted_items_count_testset,
                          'recall@5': recall_at_5,
                          'recall@10': recall_at_10}
        return person_metrics

    def evaluate_model(self, model):
        #print('Running evaluation for users')
        people_metrics = []
        for idx, userId in enumerate(list(interactions_test_indexed_df.index.unique().values)):
            #if idx % 100 == 0 and idx > 0:
            #    print('%d users processed' % idx)
            person_metrics = self.evaluate_model_for_user(model, userId)  
            person_metrics['userId'] = userId
            people_metrics.append(person_metrics)
        print('%d users processed' % idx)

        detailed_results_df = pd.DataFrame(people_metrics) \
                            .sort_values('interacted_count', ascending=False)
        
        global_recall_at_5 = detailed_results_df['hits@5_count'].sum() / float(detailed_results_df['interacted_count'].sum())
        global_recall_at_10 = detailed_results_df['hits@10_count'].sum() / float(detailed_results_df['interacted_count'].sum())
        
        global_metrics = {'modelName': model.get_model_name(),
                          'recall@5': global_recall_at_5,
                          'recall@10': global_recall_at_10}    
        return global_metrics, detailed_results_df
    
model_evaluator = ModelEvaluator()    

In [37]:
interactions_test_indexed_df

movieId    rating
userId                   
391         277  1.000000
30         2300  2.584963
481       68872  2.321928
34         1690  2.000000
468          47  2.169925
200        4226  2.459432
564        2857  2.321928
34         1387  2.000000
623         364  2.321928
653         801  2.000000
49          329  2.000000
486        3114  2.584963
43         2321  2.321928
371        2858  2.321928
306        4424  1.584963
188         292  2.000000
232        2064  2.584963
174        1094  1.584963
584         586  1.807355
179        4226  2.321928
213         344  1.000000
647        3011  2.584963
530          14  2.321928
30         1834  2.321928
214        2376  2.000000
564        1717  2.321928
38         1704  2.169925
427        2165  2.321928
632        2501  2.584963
374        5312  2.584963
165         434  1.584963
120         231  1.584963
38        89759  2.584963
187        2329  2.584963
564        1120  2.584963
306        1610  2.000000
402        4571  2.169925
56         4022  2.321928
199      106489  2.321928
505       55451  2.459432
21          597  2.000000
615      106916  2.000000
185        4655  2.000000
593         277  2.321928
598        2445  1.584963
572      109487  2.459432
475       39435  1.584963
373        1225  2.321928
287       60674  2.584963
525         260  2.584963
73        59387  2.169925
609         290  2.584963
635        2329  2.321928
547        2502  1.807355
72        52281  2.169925
271        2985  2.169925
468        6297  1.584963
574        2411  2.000000
166        5349  2.321928
587         541  2.321928
303        5991  2.321928
248        3836  2.321928
531        1258  0.584963
468        6460  2.321928
236        2066  2.459432
189        3578  2.584963
212         555  2.000000
271        1909  1.807355
73         4444  2.321928
285        2657  2.321928
165        2421  2.321928
426       71254  2.000000
588        1036  2.321928
475       86298  1.584963
105        3201  2.321928
213        1025  1.584963
519         924  2.584963
333        1954  2.584963
481         680  2.321928
91        50806  1.584963
338          47  2.321928
468        6157  1.321928
283        4246  1.807355
373        2137  2.321928
608        3578  2.321928
48         7235  2.000000
650           4  1.000000
654        4148  2.321928
5          1193  2.000000
195         924  2.584963
564        2628  1.584963
649         252  2.000000
152        1682  2.169925
382        4963  2.000000
15         4322  2.321928
105        2329  2.321928
378        2502  2.000000
15         5291  2.169925
431        6377  2.321928
316       98809  2.321928
30         1010  2.000000
461        3752  1.807355
193         105  2.321928
654         316  2.321928
132       61323  2.459432
537        1197  2.584963
56         1230  1.584963
543        1073  2.000000
339        6365  2.169925
452        2276  2.000000
457        1777  2.169925
547        1284  2.321928
73         1194  2.321928
196        3671  2.584963
562          95  2.169925
15         2288  2.000000
307       46578  2.169925
66         2947  2.584963
232        1552  2.000000
587        7234  2.169925
613        1148  2.321928
15         7361  2.584963
273        6333  2.459432
394        2571  2.584963
250       33679  2.321928
547        2795  2.169925
30         3476  1.584963
536         181  1.000000
408        2447  1.000000
599       78041  2.000000
390        1240  2.000000
73        50651  2.000000
15         2273  1.807355
596        2805  2.000000
350        3948  2.321928
132         595  2.000000
598        3408  2.321928
480        1036  2.584963
446       63082  2.584963
279         160  1.584963
496         455  2.000000
111        4228  2.169925
73        91529  2.321928
358         595  2.584963
496         338  2.584963
533        1676  2.321928
560         356  2.321928
73        43936  2.000000
662         553  1.584963
518        2917  2.000000
562       31420  2.169925
119         492  2.321928
274 

# Collaborative Filtering

In [18]:
#Creating a sparse pivot table with users in rows and items in columns
users_items_pivot_matrix_df = interactions_train_df.pivot(index='userId', 
                                                          columns='movieId', 
                                                          values='rating').fillna(0)

users_items_pivot_matrix_df.head(10)

movieId    1       2         3       4       5       6       7       8       \
userId                                                                        
1        0.000000     0.0  0.000000     0.0     0.0     0.0     0.0     0.0   
2        0.000000     0.0  0.000000     0.0     0.0     0.0     0.0     0.0   
3        0.000000     0.0  0.000000     0.0     0.0     0.0     0.0     0.0   
4        0.000000     0.0  0.000000     0.0     0.0     0.0     0.0     0.0   
5        0.000000     0.0  2.321928     0.0     0.0     0.0     0.0     0.0   
6        0.000000     0.0  0.000000     0.0     0.0     0.0     0.0     0.0   
7        0.000000     0.0  0.000000     0.0     0.0     0.0     0.0     0.0   
8        0.000000     0.0  0.000000     0.0     0.0     0.0     0.0     0.0   
9        2.321928     0.0  0.000000     0.0     0.0     0.0     0.0     0.0   
10       0.000000     0.0  0.000000     0.0     0.0     0.0     0.0     0.0   

movieId  9         10      11      12      13      14      15      16      \
userId                                                                      
1           0.0  0.000000     0.0     0.0     0.0     0.0     0.0     0.0   
2           0.0  0.000000     0.0     0.0     0.0     0.0     0.0     0.0   
3           0.0  0.000000     0.0     0.0     0.0     0.0     0.0     0.0   
4           0.0  2.321928     0.0     0.0     0.0     0.0     0.0     0.0   
5           0.0  0.000000     0.0     0.0     0.0     0.0     0.0     0.0   
6           0.0  0.000000     0.0     0.0     0.0     0.0     0.0     0.0   
7           0.0  2.000000     0.0     0.0     0.0     0.0     0.0     0.0   
8           0.0  0.000000     0.0     0.0     0.0     0.0     0.0     0.0   
9           0.0  0.000000     0.0     0.0     0.0     0.0     0.0     0.0   
10          0.0  0.000000     0.0     0.0     0.0     0.0     0.0     0.0   

movieId    17      18      19      20      21      22      23      24      \
userId                                                                      
1        0.000000     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
2        0.000000     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
3        0.000000     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
4        0.000000     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
5        0.000000     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
6        0.000000     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
7        0.000000     0.0     0.0     0.0     2.0     0.0     0.0     0.0   
8        0.000000     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
9        2.321928     0.0     0.0     0.0     0.0     0.0     0.0     0.0   
10       0.000000     0.0     0.0     0.0     0.0     0.0     0.0     0.0   

movieId  25      26      27      28      29      30      31        32      \
userId                                                                      
1           0.0     0.0     0.0     0.0     0.0     0.0     0.0  0.000000   
2           0.0     0.0     0.0     0.0     0.0     0.0     0.0  0.000000   
3           0.0     0.0     0.0     0.0     0.0     0.0     0.0  0.000000   
4           0.0     0.0     0.0     0.0     0.0     0.0     0.0  0.000000   
5           0.0     0.0     0.0     0.0     0.0     0.0     0.0  0.000000   
6           0.0     0.0     0.0     0.0     0.0     0.0     0.0  0.000000   
7           0.0     0.0     0.0     0.0     0.0     0.0     2.0  0.000000   
8           0.0     0.0     0.0     0.0     0.0     0.0     0.0  2.584963   
9           0.0     2.0     0.0     0.0     0.0     0.0     0.0  0.000000   
10          0.0     0.0     0.0     0.0     0.0     0.0     0.0  0.000000   

movieId    34      35        36      37      38        39      40      41      \
userId                                                                          
1        0.000000     0.0  0.000000     0.0     0.0  0.000000     0.0     0.0   
2        0.000000     0.0  0.0000

In [19]:
users_items_pivot_matrix = users_items_pivot_matrix_df.values
users_items_pivot_matrix[:10]

array([[0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       ...,
       [0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [2.32192809, 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ]])

In [20]:
users_ids = list(users_items_pivot_matrix_df.index)
users_ids[:10]

[1, 2, 3, 4, 5, 6, 7, 8, 9, 10]

In [21]:
users_items_pivot_sparse_matrix = csr_matrix(users_items_pivot_matrix)
users_items_pivot_sparse_matrix

<671x8374 sparse matrix of type '<class 'numpy.float64'>'
	with 80003 stored elements in Compressed Sparse Row format>

In [22]:
#The number of factors to factor the user-item matrix.
NUMBER_OF_FACTORS_MF = 15
#Performs matrix factorization of the original user item matrix
#U, sigma, Vt = svds(users_items_pivot_matrix, k = NUMBER_OF_FACTORS_MF)
U, sigma, Vt = svds(users_items_pivot_sparse_matrix, k = NUMBER_OF_FACTORS_MF)

In [23]:
U.shape

(671, 15)

In [24]:
Vt.shape

(15, 8374)

In [25]:
sigma = np.diag(sigma)
sigma.shape

(15, 15)

In [26]:
all_user_predicted_ratings = np.dot(np.dot(U, sigma), Vt) 
all_user_predicted_ratings

array([[-3.40976620e-02,  6.86249740e-03,  9.31908267e-03, ...,
        -4.17173900e-04, -3.22769788e-04, -1.70577409e-03],
       [ 7.18017820e-01,  7.25407288e-01,  2.50650603e-01, ...,
         5.85401427e-04,  4.52928371e-04, -8.72385001e-03],
       [ 5.04715415e-01,  2.03576458e-01,  6.02918050e-02, ...,
         1.31022332e-03,  1.01372714e-03,  3.78980344e-04],
       ...,
       [ 1.27417284e-01, -2.56605391e-03,  4.23853077e-02, ...,
        -5.85878581e-04, -4.53297548e-04, -6.73135750e-04],
       [ 5.29387739e-01,  9.88008162e-02,  1.20131219e-01, ...,
         1.52475477e-05,  1.17971133e-05, -9.64630999e-03],
       [ 1.66006798e+00,  2.84853746e-02,  1.04970587e-01, ...,
         1.19892353e-03,  9.27613870e-04, -1.09205242e-02]])

In [27]:
all_user_predicted_ratings_norm = (all_user_predicted_ratings - all_user_predicted_ratings.min()) / (all_user_predicted_ratings.max() - all_user_predicted_ratings.min())

In [28]:
#Converting the reconstructed matrix back to a Pandas dataframe
cf_preds_df = pd.DataFrame(all_user_predicted_ratings_norm, columns = users_items_pivot_matrix_df.columns, index=users_ids).transpose()
cf_preds_df.head(10)

1         2         3         4         5         6         7    \
movieId                                                                         
1        0.376622  0.479014  0.449975  0.496347  0.463930  0.401025  0.530624   
2        0.382199  0.480020  0.408979  0.450324  0.419157  0.383263  0.436573   
3        0.382533  0.415387  0.389472  0.401925  0.392156  0.384121  0.415099   
4        0.381502  0.394001  0.383631  0.392921  0.384051  0.381281  0.390680   
5        0.379678  0.422181  0.387812  0.385390  0.413639  0.382938  0.388150   
6        0.383261  0.459185  0.409346  0.369330  0.384128  0.383319  0.440855   
7        0.381919  0.410443  0.386621  0.409984  0.395535  0.380481  0.412200   
8        0.380862  0.387261  0.381655  0.377296  0.384902  0.380743  0.381864   
9        0.381132  0.389076  0.382301  0.376884  0.378663  0.380065  0.390986   
10       0.381963  0.516347  0.415593  0.450915  0.408914  0.387001  0.453101   

              8         9         10        11        12        13        14   \
movieId                                                                         
1        0.520150  0.455013  0.412659  0.395552  0.393666  0.456644  0.403550   
2        0.393094  0.387541  0.385718  0.386898  0.385007  0.410405  0.382771   
3        0.378896  0.394672  0.383595  0.383599  0.385770  0.384312  0.387758   
4        0.381288  0.384248  0.381788  0.381213  0.381937  0.383228  0.381510   
5        0.388943  0.394842  0.377729  0.382197  0.384431  0.393950  0.385976   
6        0.400905  0.405392  0.394923  0.391069  0.386517  0.387165  0.378556   
7        0.379730  0.395797  0.384295  0.380132  0.385840  0.389681  0.387435   
8        0.380778  0.382330  0.379993  0.380737  0.381157  0.382729  0.381513   
9        0.376619  0.385795  0.382385  0.381131  0.381736  0.379785  0.382722   
10       0.399060  0.385206  0.392238  0.380225  0.381081  0.393270  0.379877   

              15        16        17        18        19        20        21   \
movieId                                                                         
1        0.492907  0.404084  0.410544  0.460114  0.693712  0.532854  0.507382   
2        0.582725  0.384271  0.394322  0.395638  0.537625  0.426690  0.447739   
3        0.265801  0.378970  0.384581  0.425906  0.479779  0.410415  0.398751   
4        0.404973  0.381641  0.379963  0.385403  0.412036  0.387847  0.391573   
5        0.555674  0.384107  0.344533  0.406426  0.413889  0.396589  0.362450   
6        0.402785  0.389081  0.550692  0.441281  0.610598  0.425600  0.468817   
7        0.356193  0.378385  0.352826  0.416154  0.472539  0.412025  0.399496   
8        0.382549  0.381481  0.376693  0.384581  0.386076  0.383751  0.378843   
9        0.356036  0.379370  0.378980  0.397541  0.409241  0.389750  0.384881   
10       0.667039  0.383940  0.472957  0.397283  0.568777  0.433210  0.480391   

              22        23        24        25        26        27        28   \
movieId                                                                         
1        0.508815  0.554738  0.425978  0.414480  0.530189  0.417946  0.417691   
2        0.449130  0.427311  0.411510  0.385272  0.437278  0.381395  0.379683   
3        0.395530  0.381578  0.397557  0.401652  0.395417  0.383331  0.376897   
4        0.381696  0.386168  0.385376  0.382799  0.380572  0.382770  0.383195   
5        0.371068  0.344161  0.392099  0.387384  0.388337  0.387829  0.375050   
6        0.469822  0.598023  0.423957  0.409369  0.465600  0.391985  0.387178   
7        0.383812  0.387477  0.392499  0.393127  0.378026  0.379153  0.385433   
8        0.379622  0.383701  0.383022  0.381658  0.380506  0.380851  0.380534   
9        0.384844  0.374251  0.386430  0.387660  0.382854  0.380525  0.379562   
10       0.507234  0.513790  0.429983  0.388571  0.441394  0.391538  0.371944   

              29        30        31        32        33        34        35   \
movieId                                  

In [29]:
len(cf_preds_df.columns)

671

In [31]:
class CFRecommender:
    
    MODEL_NAME = 'Collaborative Filtering'
    
    def __init__(self, cf_predictions_df, items_df=None):
        self.cf_predictions_df = cf_predictions_df
        self.items_df = items_df
        
    def get_model_name(self):
        return self.MODEL_NAME
    
    def recommend_items(self, user_id, items_to_ignore=[], topn=10, verbose=False, metric=0):
        # Get and sort the user's predictions
        sorted_user_predictions = self.cf_predictions_df[user_id].sort_values(ascending=False) \
                                    .reset_index().rename(columns={user_id: 'recStrength'})
        
        # Local model recommendation use
        if(metric==0):
            ignore_interacted_items = self.items_df[self.items_df['userId'] == user_id]['movieId'].tolist()
        
        # Recommend the highest predicted rating movies that the user hasn't seen yet.
            recommendations_df = sorted_user_predictions[~sorted_user_predictions['movieId'].isin(ignore_interacted_items)] \
                                   .sort_values('recStrength', ascending = False) \
                                   .head(topn)
        # Global Metric Evaluation use
        elif(metric==1):
            recommendations_df = sorted_user_predictions[~sorted_user_predictions['Game-id'].isin(items_to_ignore)] \
                                   .sort_values('recStrength', ascending = False) \
                                   .head(topn)

        if verbose:
            if self.items_df is None:
                raise Exception('"items_df" is required in verbose mode')

            recommendations_df = recommendations_df.merge(self.items_df, how = 'left', 
                                                          left_on = 'Game-id', 
                                                          right_on = 'Game-id')[['recStrength', \
                                                                                   'movieId', \
                                                                                   'title', \
                                                                                   'genres', \
                                                                                   'overview']]

        #return self.items_df
        return recommendations_df.drop_duplicates()
    
cf_recommender_model = CFRecommender(cf_preds_df, df_movies)

In [40]:
print('Evaluating Collaborative Filtering (SVD Matrix Factorization) model...')
cf_global_metrics, cf_detailed_results_df = model_evaluator.evaluate_model(cf_recommender_model)
print('\nGlobal metrics:\n%s' % cf_global_metrics)
cf_detailed_results_df.head(10)

Evaluating Collaborative Filtering (SVD Matrix Factorization) model...


KeyError: 'userId column is missing from interactions_test_indexed_df'

In [48]:
interactions_test_indexed_df.index

Int64Index([391,  30, 481,  34, 468, 200, 564,  34, 623, 653,
            ...
            587, 427, 260, 185, 615, 468, 102, 408, 247, 382],
           dtype='int64', name='userId', length=20001)